Research Question Ideas:

How does the popularity and reception of a movie relate to its budget/revenue?

In [263]:
''' 
https://www.kaggle.com/rounakbanik/the-movies-dataset
 
Loading datasets
'''


import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import plotly.express as px

In [264]:
# Ran into EOF inside string error, set engine to python to avoid it

mov_metadata = pd.read_csv("movies_metadata.csv", engine='python')

In [265]:
mov_metadata.head()

'''
Need to filter out adult films (done)

Drop homepage/overview/poster_path/tagline belongs_to_collection/
production_companies/spoken_languages/original_language, original title, video 
(done)

Explore genres, id/imdb_id, popularity, production_countries, 
budget/revenue (done)

Drop unreleased movies (status column) (done)

Rearrange parameters for readability

On budget: Some extremely relevant films have been made on shoestring budgets
Eraserhead by David Lynch was done with $10,000 (forget filtering budget?)

Box office data from TMDB will be found in less frequency in movies 15+ years
old
"Movie grosses reporting isn't an exact science. Studios and distributors have 
started disclosing detailed figures only recently; the information for films 
released over 15 years ago are therefore very sketchy. The longer you go back 
in time, the less reliable the information becomes." - IMDB

Ideas for data exploration:
Budget vs Revenue exploration and inferences
Genre vs Budget/Revenue
Original or Spoken Language/Production Countries (analysis of data by location/culture)
Release Date (analyze data over time periods)
What are the most common runtimes?  How does runtime relate to budget?
Popularity
Vote Average/Vote Count (relate to budget, genre, release data, etc?)
'''

'\nNeed to filter out adult films (done)\n\nDrop homepage/overview/poster_path/tagline belongs_to_collection/\nproduction_companies/spoken_languages/original_language, original title, video \n(done)\n\nExplore genres, id/imdb_id, popularity, production_countries, \nbudget/revenue (done)\n\nDrop unreleased movies (status column) (done)\n\nRearrange parameters for readability\n\nOn budget: Some extremely relevant films have been made on shoestring budgets\nEraserhead by David Lynch was done with $10,000 (forget filtering budget?)\n\nBox office data from TMDB will be found in less frequency in movies 15+ years\nold\n"Movie grosses reporting isn\'t an exact science. Studios and distributors have \nstarted disclosing detailed figures only recently; the information for films \nreleased over 15 years ago are therefore very sketchy. The longer you go back \nin time, the less reliable the information becomes." - IMDB\n\nIdeas for data exploration:\nBudget vs Revenue exploration and inferences\n

In [266]:
mov_metadata.isnull().sum()

'''
A lot of these columns will be dropped anyways

Dropping unreleased and adult movies fixes a lot of our null issues, let's see
what things look like after
'''

"\nA lot of these columns will be dropped anyways\n\nDropping unreleased and adult movies fixes a lot of our null issues, let's see\nwhat things look like after\n"

In [267]:
# Dataframe shape

mov_metadata.shape

(45466, 24)

In [268]:
# Dropping irrelevant columns

mov_metadata = mov_metadata.drop([
                                  'homepage', 
                                  'overview', 
                                  'poster_path', 
                                  'tagline',
                                  'belongs_to_collection',
                                  'production_companies',
                                  'spoken_languages',
                                  'original_language',
                                  'original_title',
                                  'video',
                                  ], 
                                 axis=1)

In [269]:
# Looking at values for 'adult' and 'status' columns

print(mov_metadata['adult'].value_counts())
print(mov_metadata['status'].value_counts())

# We can get rid of all the movies that aren't released and adult movies

False                                                                                                                             45454
True                                                                                                                                  9
 - Written by Ørnås                                                                                                                   1
 Rune Balot goes to a casino connected to the October corporation to try to wrap up her case once and for all.                        1
 Avalanche Sharks tells the story of a bikini contest that turns into a horrifying affair when it is hit by a shark avalanche.        1
Name: adult, dtype: int64
Released           45014
Rumored              230
Post Production       98
In Production         20
Planned               15
Canceled               2
Name: status, dtype: int64


In [270]:
# Removing adult films, unreleased filmes

mov_metadata = mov_metadata.drop(mov_metadata['adult'][mov_metadata['adult']!='False'].index)
mov_metadata = mov_metadata.drop(mov_metadata['status'][mov_metadata['status']!='Released'].index)

In [271]:
mov_metadata = mov_metadata.drop(['adult', 'status'], axis=1)

In [272]:
mov_metadata.isnull().sum()

'''
15 missing IMDB IDs
78 missing release dates
251 missing runtimes

let's get a closer look at these observations
'''

"\n15 missing IMDB IDs\n78 missing release dates\n251 missing runtimes\n\nlet's get a closer look at these observations\n"

In [273]:
# A view of all the observations that are missing IMDB IDs

mov_metadata[mov_metadata['imdb_id'].isnull()==True]

budget  ... vote_count
8966   1000000  ...        3.0
13757        0  ...        2.0
13821        0  ...        3.0
17382  2500000  ...        1.0
18959        0  ...       12.0
19322        0  ...       19.0
20806        0  ...       48.0
20937        0  ...        3.0
21916        0  ...        1.0
23744        0  ...        5.0
33753        0  ...        0.0
36955        0  ...        0.0
40809        0  ...       37.0
41832        0  ...        0.0
45070        0  ...        0.0

[15 rows x 12 columns]

In [274]:
# I do some googling to find if a movie has an IMDB ID or not and fill in the
# data appropriately

mov_metadata.loc[8966, 'imdb_id']='tt0101704'
mov_metadata.loc[13757, 'imdb_id']='tt0358146'
mov_metadata.loc[18959, 'imdb_id']='tt0490048'
mov_metadata.loc[20937, 'imdb_id']='tt0119501'
mov_metadata.loc[21916, 'imdb_id']='tt0105298'
mov_metadata.loc[33753, 'imdb_id']='tt6618142'
mov_metadata.loc[36955, 'imdb_id']='tt1147516'
mov_metadata.loc[41832, 'imdb_id']='tt4699464'
mov_metadata.loc[45070, 'imdb_id']='tt6051554'

# These entries are smaller parts of bigger movies, not featured on IMDB and
# resulting in some missing data

mov_metadata = mov_metadata.drop(13821)
mov_metadata = mov_metadata.drop(20806)

# Couldn't find any info on these entries

mov_metadata = mov_metadata.drop(17382)
mov_metadata = mov_metadata.drop(19322)
mov_metadata = mov_metadata.drop(23744)
mov_metadata = mov_metadata.drop(40809)

In [275]:
mov_metadata[mov_metadata['budget']=='0']

budget  ... vote_count
2          0  ...       92.0
4          0  ...      173.0
7          0  ...       45.0
11         0  ...      210.0
12         0  ...      423.0
...      ...  ...        ...
45461      0  ...        1.0
45462      0  ...        3.0
45463      0  ...        6.0
45464      0  ...        0.0
45465      0  ...        0.0

[36137 rows x 12 columns]

In [276]:
# After doing some research it looks like a budget of 0 is simply unfound data,
# we should change these to NaNs to exclude them from analysis if necessary

mov_metadata.loc[mov_metadata['budget'] == '0','budget'] = np.NaN

In [277]:
# It looks like we only have good budget data for ~9000 movie entries or 20% of
# our dataset - but the budget data we DO have should still be relevant

mov_metadata['budget'].value_counts()

5000000     286
10000000    259
20000000    243
2000000     241
15000000    226
           ... 
33            1
4185000       1
2090000       1
280           1
9272437       1
Name: budget, Length: 1218, dtype: int64

In [278]:
mov_metadata[mov_metadata['revenue']==0]

budget  ... vote_count
2           NaN  ...       92.0
6      58000000  ...      141.0
7           NaN  ...       45.0
11          NaN  ...      210.0
21          NaN  ...      199.0
...         ...  ...        ...
45461       NaN  ...        1.0
45462       NaN  ...        3.0
45463       NaN  ...        6.0
45464       NaN  ...        0.0
45465       NaN  ...        0.0

[37605 rows x 12 columns]

In [279]:
mov_metadata.loc[mov_metadata['revenue'] == 0,'revenue'] = np.NaN

In [280]:
mov_metadata['runtime'].value_counts()

90.0      2530
0.0       1495
100.0     1457
95.0      1400
93.0      1202
          ... 
238.0        1
316.0        1
258.0        1
780.0        1
1256.0       1
Name: runtime, Length: 353, dtype: int64

In [281]:
mov_metadata[mov_metadata['runtime']==0]

budget  ... vote_count
222       NaN  ...        1.0
224       NaN  ...        9.0
398       NaN  ...        1.0
554       NaN  ...        1.0
667       NaN  ...        2.0
...       ...  ...        ...
45370     NaN  ...        2.0
45371     NaN  ...        2.0
45399  750000  ...        4.0
45416     NaN  ...        0.0
45430     NaN  ...        1.0

[1495 rows x 12 columns]

In [282]:
'''
Around 1500 movies missing their runtimes, not much I can do to fill in the
data with that much missing so we'll simply convert them to NaNs
These will get bundled together with the other observations that were already
NaNs and we can filter these out as needed
'''

mov_metadata.loc[mov_metadata['runtime'] == 0, 'runtime'] = np.NaN

In [283]:
# We probably want to turn these empty lists into NaNs

mov_metadata['genres'].value_counts()

[{'id': 18, 'name': 'Drama'}]                                                                                                                                      4941
[{'id': 35, 'name': 'Comedy'}]                                                                                                                                     3585
[{'id': 99, 'name': 'Documentary'}]                                                                                                                                2677
[]                                                                                                                                                                 2383
[{'id': 18, 'name': 'Drama'}, {'id': 10749, 'name': 'Romance'}]                                                                                                    1292
                                                                                                                                                                

In [284]:
# Get those NaNs setup

mov_metadata.loc[mov_metadata['genres'] == '[]', 'genres'] = np.NaN

# We're left with 4044 observations with genre data, usable but a small subset
# of all our actual data

In [285]:
# We have a number of 0 values here, but they're actually relevant data in this
# context and don't necessarily need to be converted to NaNs

mov_metadata['popularity'].value_counts()

0.0         64
1e-06       56
0.000308    42
0.00022     39
0.000578    37
            ..
0.372215     1
0.541651     1
0.932111     1
0.19332      1
5.745206     1
Name: popularity, Length: 43347, dtype: int64

In [286]:
# Converting this column from string to float 

mov_metadata['popularity'] = np.array(mov_metadata['popularity'], dtype=np.float32)

In [287]:
mov_metadata['popularity'].max()

547.48828125

In [288]:
mov_metadata['production_countries'].value_counts()

[{'iso_3166_1': 'US', 'name': 'United States of America'}]                                                                                                            17730
[]                                                                                                                                                                     6146
[{'iso_3166_1': 'GB', 'name': 'United Kingdom'}]                                                                                                                       2228
[{'iso_3166_1': 'FR', 'name': 'France'}]                                                                                                                               1638
[{'iso_3166_1': 'JP', 'name': 'Japan'}]                                                                                                                                1349
                                                                                                                                            

In [289]:
mov_metadata.head()

budget  ... vote_count
0  30000000  ...     5415.0
1  65000000  ...     2413.0
2       NaN  ...       92.0
3  16000000  ...       34.0
4       NaN  ...      173.0

[5 rows x 12 columns]

In [290]:
# Rearranging column labels for readability

mov_metadata = mov_metadata[[
                             'id', 
                             'imdb_id', 
                             'title', 
                             'release_date', 
                             'runtime', 
                             'production_countries', 
                             'genres', 'budget', 
                             'revenue', 
                             'popularity',
                             'vote_average',
                             'vote_count'
                             ]]

In [291]:
mov_metadata.head()

id    imdb_id  ... vote_average vote_count
0    862  tt0114709  ...          7.7     5415.0
1   8844  tt0113497  ...          6.9     2413.0
2  15602  tt0113228  ...          6.5       92.0
3  31357  tt0114885  ...          6.1       34.0
4  11862  tt0113041  ...          5.7      173.0

[5 rows x 12 columns]

In [292]:
# Converting budget, revenue, and user vote to float so we can perform 
# operations using them

mov_metadata['budget'] = np.array(mov_metadata['budget'], dtype=np.float32)
mov_metadata['revenue'] = np.array(mov_metadata['revenue'], dtype=np.float32)
mov_metadata['vote_count'] = np.array(mov_metadata['vote_count'], dtype=np.float32)

In [293]:
# Engineering some useful features

mov_metadata['profit'] = mov_metadata['revenue'] - mov_metadata['budget']
mov_metadata['budget per minute of runtime'] = mov_metadata['budget'] / mov_metadata['runtime']
mov_metadata['budget per user vote'] = mov_metadata['budget'] / mov_metadata['vote_count'][mov_metadata['vote_count']!=0]
mov_metadata['revenue per minute of runtime'] = mov_metadata['revenue'] / mov_metadata['runtime']
mov_metadata['revenue per user vote'] = mov_metadata['revenue'] / mov_metadata['vote_count'][mov_metadata['vote_count']!=0]
mov_metadata['profit per minute of runtime'] = mov_metadata['profit'] / mov_metadata['runtime']
mov_metadata['profit per user vote'] = mov_metadata['profit'] / mov_metadata['vote_count'][mov_metadata['vote_count']!=0]

In [294]:
# Converting our features into floats with 2 decimal places

mov_metadata['budget per minute of runtime'] = np.array(['%.2f' % elem for elem in mov_metadata['budget per minute of runtime']], dtype=np.float32)
mov_metadata['budget per user vote'] = np.array(['%.2f' % elem for elem in mov_metadata['budget per user vote']], dtype=np.float32)
mov_metadata['revenue per minute of runtime'] = np.array(['%.2f' % elem for elem in mov_metadata['revenue per minute of runtime']], dtype=np.float32)
mov_metadata['revenue per user vote'] = np.array(['%.2f' % elem for elem in mov_metadata['revenue per user vote']], dtype=np.float32)
mov_metadata['profit per minute of runtime'] = np.array(['%.2f' % elem for elem in mov_metadata['profit per minute of runtime']], dtype=np.float32)
mov_metadata['profit per user vote'] = np.array(['%.2f' % elem for elem in mov_metadata['profit per user vote']], dtype=np.float32)

In [295]:
# Gathering some data insights

print("Runtime:\n",
      "Runtime Mean:\n", mov_metadata['runtime'].mean(), '\n',
      "Runtime Standard Deviation:\n", mov_metadata['runtime'].std(), '\n',
      "Runtime Maximum:\n", mov_metadata['runtime'].max(), '\n',
      "Runtime Minimum:\n", mov_metadata['runtime'].min(), '\n')

print("Budget:\n",
      "Budget Mean:\n", mov_metadata['budget'].mean(), '\n',
      "Budget Standard Deviation:\n", mov_metadata['budget'].std(), '\n',
      "Budget Maximum:\n", mov_metadata['budget'].max(), '\n',
      "Budget Minimum:\n", mov_metadata['budget'].min(), '\n')

print("Revenue:\n",
      "Revenue Mean:\n", mov_metadata['revenue'].mean(), '\n',
      "Revenue Standard Deviation:\n", mov_metadata['revenue'].std(), '\n',
      "Revenue Maximum:\n", mov_metadata['revenue'].max(), '\n',
      "Revenue Minimum:\n", mov_metadata['revenue'].min(), '\n')

print("Popularity:\n",
      "Popularity Mean:\n", mov_metadata['popularity'].mean(), '\n',
      "Popularity Standard Deviation:\n", mov_metadata['popularity'].std(), '\n',
      "Popularity Maximum:\n", mov_metadata['popularity'].max(), '\n',
      "Popularity Minimum:\n", mov_metadata['popularity'].min(), '\n')

print("Vote Average:\n",
      "Vote Average Mean:\n", mov_metadata['vote_average'].mean(), '\n',
      "Vote Average Standard Deviation:\n", mov_metadata['vote_average'].std(), '\n',
      "Vote Average Maximum:\n", mov_metadata['vote_average'].max(), '\n',
      "Vote Average Minimum:\n", mov_metadata['vote_average'].min(), '\n')

print("Vote Count:\n",
      "Vote Count Mean:\n", mov_metadata['vote_count'].mean(), '\n',
      "Vote Count Standard Deviation:\n", mov_metadata['vote_count'].std(), '\n',
      "Vote Count Maximum:\n", mov_metadata['vote_count'].max(), '\n',
      "Vote Count Minimum:\n", mov_metadata['vote_count'].min(), '\n')

print("Budget Per Minute of Runtime:\n",
      "Budget Per Minute of Runtime:\n", mov_metadata['budget per minute of runtime'].mean(), '\n',
      "Budget Per Minute of Runtime Standard Deviation:\n", mov_metadata['budget per minute of runtime'].std(), '\n',
      "Budget Per Minute of Runtime Maximum:\n", mov_metadata['budget per minute of runtime'].max(), '\n',
      "Budget Per Minute of Runtime Minimum:\n", mov_metadata['budget per minute of runtime'].min(), '\n')

print("Budget Per User Vote:\n",
      "Budget Per User Vote Mean:\n", mov_metadata['budget per user vote'].mean(), '\n',
      "Budget Per User Vote Standard Deviation:\n", mov_metadata['budget per user vote'].std(), '\n',
      "Budget Per User Vote Maximum:\n", mov_metadata['budget per user vote'].max(), '\n',
      "Budget Per User Vote Minimum:\n", mov_metadata['budget per user vote'].min(), '\n')

print("Revenue Per Minute of Runtime:\n",
      "Revenue Per Minute of Runtime Mean:\n", mov_metadata['revenue per minute of runtime'].mean(), '\n',
      "Revenue Per Minute of Runtime Standard Deviation:\n", mov_metadata['revenue per minute of runtime'].std(), '\n',
      "Revenue Per Minute of Runtime Maximum:\n", mov_metadata['revenue per minute of runtime'].max(), '\n',
      "Revenue Per Minute of Runtime Minimum:\n", mov_metadata['revenue per minute of runtime'].min(), '\n')

print("Revenue Per User Vote:\n",
      "Revenue Per User Vote Mean:\n", mov_metadata['revenue per user vote'].mean(), '\n',
      "Revenue Per User Vote Standard Deviation:\n", mov_metadata['revenue per user vote'].std(), '\n',
      "Revenue Per User Vote Maximum:\n", mov_metadata['revenue per user vote'].max(), '\n',
      "Revenue Per User Vote Minimum:\n", mov_metadata['revenue per user vote'].min(), '\n')

print("Profit Per Minute of Runtime:\n",
      "Profit Per Minute of Runtime Mean:\n", mov_metadata['profit per minute of runtime'].mean(), '\n',
      "Profit Per Minute of Runtime Standard Deviation:\n", mov_metadata['profit per minute of runtime'].std(), '\n',
      "Profit Per Minute of Runtime Maximum:\n", mov_metadata['profit per minute of runtime'].max(), '\n',
      "Profit Per Minute of Runtime Minimum:\n", mov_metadata['profit per minute of runtime'].min(), '\n')

print("Profit Per User Vote:\n",
      "Profit Per User Vote Mean:\n", mov_metadata['profit per user vote'].mean(), '\n',
      "Profit Per User Vote Standard Deviation:\n", mov_metadata['profit per user vote'].std(), '\n',
      "Profit Per User Vote Maximum:\n", mov_metadata['profit per user vote'].max(), '\n',
      "Profit Per User Vote Minimum:\n", mov_metadata['profit per user vote'].min(), '\n')

Runtime:
 Runtime Mean:
 97.53248254496694 
 Runtime Standard Deviation:
 34.703852558828466 
 Runtime Maximum:
 1256.0 
 Runtime Minimum:
 1.0 

Budget:
 Budget Mean:
 21661888.0 
 Budget Standard Deviation:
 34346320.0 
 Budget Maximum:
 380000000.0 
 Budget Minimum:
 1.0 

Revenue:
 Revenue Mean:
 68899032.0 
 Revenue Standard Deviation:
 146524368.0 
 Revenue Maximum:
 2787965184.0 
 Revenue Minimum:
 1.0 

Popularity:
 Popularity Mean:
 2.9394726753234863 
 Popularity Standard Deviation:
 6.024213790893555 
 Popularity Maximum:
 547.48828125 
 Popularity Minimum:
 0.0 

Vote Average:
 Vote Average Mean:
 5.623877777777487 
 Vote Average Standard Deviation:
 1.915971028966491 
 Vote Average Maximum:
 10.0 
 Vote Average Minimum:
 0.0 

Vote Count:
 Vote Count Mean:
 110.9212875366211 
 Vote Count Standard Deviation:
 493.7283630371094 
 Vote Count Maximum:
 14075.0 
 Vote Count Minimum:
 0.0 

Budget Per Minute of Runtime:
 Budget Per Minute of Runtime:
 196841.6875 
 Budget Per Mi

In [296]:
'''
The analysis we did above gives all sorts of useful insights:

Runtime averages somewhere around 60min to 135min - 
this is about what I'd expect

Budget averages around 21 million but with such a huge std this data isn't as
robust, I expected there to be a wide variety of budgets with such an 
expansive dataset

Revenue averages around 68 million but with a much greater standard deviation
than budget - I think this indicates how wildly the revenue of a movie can
vary regardless of budget

Vote average has our average user giving the average movie a 5.6/10 with an 
std of 1.9 - so we're seeing scores like 3.7-7.5 often

Vote count has an average of 110 with an std of 493 - another key point here
is the maximum of 14075 - I think this indicates a disproportionality with 
blockbusters receiving huge amounts of votes and then the rest of cinema 
receiving a much smaller share of attention

We have a lot of engineered features here, but with high std values -
we'll save these features for when we need them
'''

"\nThe analysis we did above gives all sorts of useful insights:\n\nRuntime averages somewhere around 60min to 135min - \nthis is about what I'd expect\n\nBudget averages around 21 million but with such a huge std this data isn't as\nrobust, I expected there to be a wide variety of budgets with such an \nexpansive dataset\n\nRevenue averages around 68 million but with a much greater standard deviation\nthan budget - I think this indicates how wildly the revenue of a movie can\nvary regardless of budget\n\nVote average has our average user giving the average movie a 5.6/10 with an \nstd of 1.9 - so we're seeing scores like 3.7-7.5 often\n\nVote count has an average of 110 with an std of 493 - another key point here\nis the maximum of 14075 - I think this indicates a disproportionality with \nblockbusters receiving huge amounts of votes and then the rest of cinema \nreceiving a much smaller share of attention\n\nWe have a lot of engineered features here, but with high std values -\nwe'll

In [297]:
fig = px.scatter(mov_metadata, 
                 x='vote_average', 
                 y='revenue', 
                 size='vote_count', 
                 hover_data=['title'],
                 labels={
                     'vote_average':'Average User Score',
                     'revenue':'Revenue',},
                 title='User Score vs Revenue',)

fig.show()

In [298]:
fig = px.scatter(mov_metadata, 
                 x='vote_count', 
                 y='revenue',
                 color='vote_average',  
                 hover_data=['title'],
                 labels={
                     'vote_count':'Amount of User Votes',
                     'revenue':'Revenue',
                     'vote_average':'Average User Score'},
                 title='Amount of User Votes vs Revenue')

fig.show()

In [299]:
fig = px.scatter(mov_metadata, 
                 x='vote_count', 
                 y='vote_average',
                 title='Amount of User Votes vs Average Score',
                 labels={
                     'vote_count':'Amount of User Votes',
                     'vote_average':'Average Score',},
                 hover_data=['title'])

fig.show()